# SentSim

## Imports and Setup

In [ ]:
from sentence_transformers import SentenceTransformer, util
import pandas as pd
import numpy as np
import os
import sys

In [ ]:
# Column index of feedback in CSV
data_column = 2
# Header row number to start parsing after
data_row = 1
# How many total test examples are provided
num_tests = 5
test_file = 'tests.csv'
# Path to desired SentenceTransformer model (relative to MYPATH)
model_path = 'models/sentence-transformers_all-mpnet-base-v2'

In [ ]:
# Get the path to the install folder set in run.sh
MYPATH = os.getenv('MYPATH')
directory = MYPATH+'/data'

In [ ]:
file_list = os.listdir(directory)
file_path = os.path.join(directory, file_list[0])
print(file_path)

## Data Input

In [5]:
data = pd.read_csv(file_path, keep_default_na=False, header=None, encoding = 'unicode_escape', engine ='python')
data

0      1                                                  2         3
0      ID  Score                                           Feedback     Notes
1       1      2  I would change the dining hall to have more ty...     Apple
2      17      2               I dont like having to walk to class.    Banana
3      39      9                                         More buses  Cucumber
4  235423      6  There are too many mosquitoes on campus. They ...      Duck

In [6]:
tests = pd.read_csv(MYPATH+test_file, keep_default_na=False, header=None, encoding = 'unicode_escape', engine ='python')
tests

0
0  size of classes
1     mass transit
2    public safety
3  quality of food
4   robot uprising

In [7]:
tests_text = tests.loc[:][0]
# SentenceTransformer wants indexing to start at 0, so we reset
#     the index and drop the old indices
feedback_text = data.loc[data_row:][data_column].reset_index(drop=True)
feedback_text

0    I would change the dining hall to have more ty...
1                 I dont like having to walk to class.
2                                           More buses
3    There are too many mosquitoes on campus. They ...
Name: 2, dtype: object

## Using the model

In [8]:
# path to the folder that contains the config.json file
# This uses the following HF model:
#  https://huggingface.co/sentence-transformers/all-mpnet-base-v2
model = SentenceTransformer(MYPATH+model_path)

In [9]:
tests = model.encode(tests_text)
feedback = model.encode(feedback_text)

In [10]:
print(tests.shape)
print(feedback.shape)
tests

(5, 768)
(4, 768)


array([[ 0.00531309,  0.01246637, -0.00990538, ...,  0.02759883,
        -0.01668295,  0.01243234],
       [-0.02030246,  0.01770941, -0.00373942, ..., -0.04288071,
        -0.03075184, -0.01293491],
       [-0.00247474,  0.00174774,  0.01997339, ..., -0.02406575,
         0.01295806, -0.00414417],
       [ 0.00664289,  0.0805131 , -0.02354824, ...,  0.03988045,
         0.04549433,  0.00696457],
       [ 0.00536655,  0.06831884,  0.02261301, ...,  0.04422512,
        -0.03214771, -0.01640472]], dtype=float32)

In [11]:
similarity = util.cos_sim(feedback, tests)
similarity

tensor([[ 0.1447,  0.0726,  0.0951,  0.1393,  0.0647],
        [ 0.1878,  0.3848,  0.1217, -0.0127,  0.0539],
        [ 0.2149,  0.5412,  0.3327,  0.1264,  0.1854],
        [ 0.1083,  0.0889,  0.1487,  0.0124,  0.0532]])

In [12]:
print(tests_text)
print(feedback_text)

0    size of classes
1       mass transit
2      public safety
3    quality of food
4     robot uprising
Name: 0, dtype: object
0    I would change the dining hall to have more ty...
1                 I dont like having to walk to class.
2                                           More buses
3    There are too many mosquitoes on campus. They ...
Name: 2, dtype: object


## Examples of behavior
### World Knowledge

In [13]:
def my_compare(a,b):
    temp =  util.cos_sim(model.encode(a), model.encode(b)).tolist()[0]
    for num in temp:
        print(f'{num:.4f}')

def my_compare2(a,b):
    return util.cos_sim(model.encode(a), model.encode(b))

In [14]:
a = "The first president of the United States had dogs."
b = "George Washington owned four French hounds."
my_compare(a,b)

0.7027


In [15]:
c = "Michael Phelps swam really well."
my_compare(c,[a,b])

0.1135
0.0883


### Score scaling

In [16]:
d = "trichloroaetic acid isopropyl ester"
my_compare(d,[a,c])

-0.0642
-0.0111


In [17]:
e = "John Adams wrote 1100 letters to his wife."
my_compare(e,[a,b,c])

0.2757
0.3410
0.0324


In [18]:
f = "George Washington owned three houses."
my_compare(f,[a,b,c])

0.4964
0.6256
0.0925


### Score dilution

In [20]:
g = "George Washington owned four French hounds. A big old well-worn sofa is very comfy to sit in."
my_compare(g,[a,b,c])

0.5964
0.7646
0.0587


### Score smearing

In [21]:
h = "George Washington owned four French hounds. Michael Phelps swam really well."
my_compare(h,[a,b,c,d,e])

0.6073
0.7359
0.5617
-0.0794
0.2085


### Ordering matters

In [22]:
h = "Michael Phelps swam really well. George Washington owned four French hounds."
my_compare(h,[a,b,c,d,e])

0.5532
0.6585
0.6619
-0.0727
0.2046


### Further smearing

In [23]:
i = "Michael Phelps swam really well. George Washington owned four French hounds. trichloroaetic acid isopropyl ester"
my_compare2([h,i],[a,b,c,d,e])

tensor([[ 0.5532,  0.6585,  0.6619, -0.0727,  0.2046],
        [ 0.5001,  0.5478,  0.5280,  0.3385,  0.1875]])

In [26]:
a = "giant happy sweet lady dancing on summer day"
b = "tiny miserable sour man comatose under winter night"
my_compare(a,b)

0.1431
